# Titanic<sub>An introduction to machine learning <sub>
[Home Page](https://www.kaggle.com/c/titanic)




<img src="https://i0.wp.com/intheboatshed.net/wp-content/uploads/2008/04/titanic_4.jpg" width="800px">

# Interesting Links

kaggle intern:
 - https://www.kaggle.com/alexisbcook/titanic-tutorial
 - https://www.kaggle.com/parulpandey/10-simple-hacks-to-speed-up-your-data-analysis#758058
 
 others:
 - https://pandas-profiling.github.io/pandas-profiling/docs/


# Settings

In [1]:
# settings
from IPython.core.interactiveshell import InteractiveShell  
InteractiveShell.ast_node_interactivity = "all"
#To revert to the original setting :
# InteractiveShell.ast_node_interactivity = "last_expr"

# Imports

In [2]:
#imports
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import pandas_profiling # dataframe profiling @
import os

In [7]:
# walk file structure and find input data
input_files=[]
for dirname, _, filenames in os.walk('kaggle/input'):
    for filename in filenames:
        path=os.path.join(dirname, filename)
        if path.endswith('submission.csv'):
            path_gs=path
        elif path.endswith('test.csv'):
            path_test=path
        elif path.endswith('train.csv'):
            path_train=path
print(path_gs,path_test,path_train)            

kaggle/input\gender_submission.csv kaggle/input\test.csv kaggle/input\train.csv


# Data Frame Creation

In [8]:
# create a dataframe for each csv file
df_gs=pd.read_csv(path_gs)
df_test=pd.read_csv(path_test)
df_train=pd.read_csv(path_train)

# display
# df_gs.head()
# df_test.head()
#df_train.head()

# DataFrame Profile Report

In [9]:
#profile report fpor each df
# source : https://pypi.org/project/pandas-profiling/
#df_test.profile_report(title='Titanic test')

In [10]:
#profile report for notebook export
# source : https://pypi.org/project/pandas-profiling/

# #gender sub
# profile_gs = df_gs.profile_report(title='Titanic gender submission')
# profile_gs.to_file(output_file="kaggle/profile_report/Titanic gender submission.html")

# #gender sub
# profile_test = df_test.profile_report(title='Titanic test')
# profile_test.to_file(output_file="kaggle/profile_report/Titanic test.html")

# #gender sub
# profile_train = df_train.profile_report(title='Titanic train')
# profile_train.to_file(output_file="kaggle/profile_report/Titanic train.html")

# A simple aproach

## Wrangling

In [11]:
def df_wrangle(df):
    df.loc[df.Sex=='female','Sex_num']=200
    df.loc[df.Sex=='male','Sex_num']=100
    df.loc[df.Age<21,'Age_num']=10
    df.loc[df.Age>=21,'Age_num']=20
    df.loc[df.Age.isna(),'Age_num']=30
    df['crit']=df.Sex_num+df.Pclass+df.Age_num
    df.drop(['Age_num','Sex_num'],axis=1,inplace=True)
    return df

In [12]:
df=pd.read_csv(path_train)
df=df_wrangle(df)
df.head()

PassengerId  Survived  Pclass  \
0            1         0       3   
1            2         1       1   
2            3         1       3   
3            4         1       1   
4            5         0       3   

                                                Name     Sex   Age  SibSp  \
0                            Braund, Mr. Owen Harris    male  22.0      1   
1  Cumings, Mrs. John Bradley (Florence Briggs Th...  female  38.0      1   
2                             Heikkinen, Miss. Laina  female  26.0      0   
3       Futrelle, Mrs. Jacques Heath (Lily May Peel)  female  35.0      1   
4                           Allen, Mr. William Henry    male  35.0      0   

   Parch            Ticket     Fare Cabin Embarked   crit  
0      0         A/5 21171   7.2500   NaN        S  123.0  
1      0          PC 17599  71.2833   C85        C  221.0  
2      0  STON/O2. 3101282   7.9250   NaN        S  223.0  
3      0            113803  53.1000  C123        S  221.0  
4      0            373450   8.0500   NaN        S  123.0

In [13]:
df_surviving_rate=df[['crit','Survived']].groupby('crit',as_index=False).mean()
df_surviving_rate.rename(columns={'Survived':'Surviving_rate'},inplace=True)
df_surviving_rate

crit  Surviving_rate
0   111.0        0.571429
1   112.0        0.526316
2   113.0        0.194805
3   121.0        0.382979
4   122.0        0.062500
5   123.0        0.130682
6   131.0        0.238095
7   132.0        0.222222
8   133.0        0.095745
9   211.0        0.928571
10  212.0        1.000000
11  213.0        0.510638
12  221.0        0.971831
13  222.0        0.896552
14  223.0        0.418182
15  231.0        1.000000
16  232.0        1.000000
17  233.0        0.595238

In [14]:
def surviving_rate(critt):   
    return df_surviving_rate.Surviving_rate.loc[df_surviving_rate.crit==critt].values[0]

 ## apply critt to df_test

In [15]:
df_test.head()

PassengerId  Pclass                                          Name     Sex  \
0          892       3                              Kelly, Mr. James    male   
1          893       3              Wilkes, Mrs. James (Ellen Needs)  female   
2          894       2                     Myles, Mr. Thomas Francis    male   
3          895       3                              Wirz, Mr. Albert    male   
4          896       3  Hirvonen, Mrs. Alexander (Helga E Lindqvist)  female   

    Age  SibSp  Parch   Ticket     Fare Cabin Embarked  
0  34.5      0      0   330911   7.8292   NaN        Q  
1  47.0      1      0   363272   7.0000   NaN        S  
2  62.0      0      0   240276   9.6875   NaN        Q  
3  27.0      0      0   315154   8.6625   NaN        S  
4  22.0      1      1  3101298  12.2875   NaN        S

In [16]:
df_test=df_wrangle(df_test)
df_test=df_test[['PassengerId','crit']]
df_test.head()

PassengerId   crit
0          892  123.0
1          893  223.0
2          894  122.0
3          895  123.0
4          896  223.0

## Prediction

In [17]:
df_test.loc[:,'Surviving_rate']=df_test.apply(lambda x: surviving_rate(x['crit']),axis=1)
df_test.loc[:,'Survived']=0
df_test.head()

PassengerId   crit  Surviving_rate  Survived
0          892  123.0        0.130682         0
1          893  223.0        0.418182         0
2          894  122.0        0.062500         0
3          895  123.0        0.130682         0
4          896  223.0        0.418182         0

In [18]:
val_list={}
for critt in df_test.crit.unique():
    lenght=len(df_test.loc[df_test.crit==critt])
    surv=round(surviving_rate(critt),3)
    val=[1]
    for i in range(lenght-1):     
        if np.mean(val)<=surv:
            val.append(1)
        else:
            val.append(0)
    real_surv=round(np.mean(val),3)        
    val_list[critt]={'length': lenght,
                    'surv':surv,
                    'real_surv':real_surv,
                    'val_list':val}
    #print(critt,lenght,surv,real_surv)
    df_test.loc[df_test.crit==critt,'Survived']=val_list[critt]['val_list']

#val_list[123]['val_list']

## submission

In [19]:
df_export=df_test[['PassengerId','Survived']]
df_export.set_index('PassengerId',inplace=True)
#.drop('index'.inplace=True)
df_export.head()
#df_gs.head()

Survived
PassengerId          
892                 1
893                 1
894                 1
895                 0
896                 0

df_export.to_csv('my_first_submission.csv')

# Machine learning aproache

In [ ]:
check : https://www.kaggle.com/startupsci/titanic-data-science-solutions

## imports

In [49]:
from sklearn.ensemble import RandomForestClassifier

## Your first machine learning model

In [90]:
train_data=pd.read_csv(path_train)
test_data=pd.read_csv(path_test)
train_data.head()
#test_data.head()

PassengerId  Survived  Pclass  \
0            1         0       3   
1            2         1       1   
2            3         1       3   
3            4         1       1   
4            5         0       3   

                                                Name     Sex   Age  SibSp  \
0                            Braund, Mr. Owen Harris    male  22.0      1   
1  Cumings, Mrs. John Bradley (Florence Briggs Th...  female  38.0      1   
2                             Heikkinen, Miss. Laina  female  26.0      0   
3       Futrelle, Mrs. Jacques Heath (Lily May Peel)  female  35.0      1   
4                           Allen, Mr. William Henry    male  35.0      0   

   Parch            Ticket     Fare Cabin Embarked  
0      0         A/5 21171   7.2500   NaN        S  
1      0          PC 17599  71.2833   C85        C  
2      0  STON/O2. 3101282   7.9250   NaN        S  
3      0            113803  53.1000  C123        S  
4      0            373450   8.0500   NaN        S

## wrangling

In [91]:
if False:
    def df_wrangle(df):
        df.loc[df.Age.isna(),'Age']='none'
        df.loc[df.Cabin.isna(),'Cabin']='none'
        return df

if True:
    def df_wrangle(df):
        df.loc[df.Age<10,'Age']=0
        df.loc[(df.Age<20) & (df.Age>=10),'Age']=10
        df.loc[(df.Age<30) & (df.Age>=20),'Age']=20
        df.loc[(df.Age<40) & (df.Age>=30),'Age']=30
        df.loc[(df.Age<50) & (df.Age>=40),'Age']=40
        df.loc[(df.Age<60) & (df.Age>=50),'Age']=50
        df.loc[(df.Age<70) & (df.Age>=60),'Age']=60
        df.loc[(df.Age<80) & (df.Age>=70),'Age']=70
        df.loc[df.Age.isna(),'Age']=100
        df.loc[df.Cabin.isna()==False,'Cabin']='yes'
        df.loc[df.Cabin.isna(),'Cabin']='no'
        return df



In [92]:
train_data=df_wrangle(train_data)
test_data=df_wrangle(test_data)
train_data.head()
test_data.head()

PassengerId  Survived  Pclass  \
0            1         0       3   
1            2         1       1   
2            3         1       3   
3            4         1       1   
4            5         0       3   

                                                Name     Sex   Age  SibSp  \
0                            Braund, Mr. Owen Harris    male  20.0      1   
1  Cumings, Mrs. John Bradley (Florence Briggs Th...  female  30.0      1   
2                             Heikkinen, Miss. Laina  female  20.0      0   
3       Futrelle, Mrs. Jacques Heath (Lily May Peel)  female  30.0      1   
4                           Allen, Mr. William Henry    male  30.0      0   

   Parch            Ticket     Fare Cabin Embarked  
0      0         A/5 21171   7.2500    no        S  
1      0          PC 17599  71.2833   yes        C  
2      0  STON/O2. 3101282   7.9250    no        S  
3      0            113803  53.1000   yes        S  
4      0            373450   8.0500    no        S

PassengerId  Pclass                                          Name     Sex  \
0          892       3                              Kelly, Mr. James    male   
1          893       3              Wilkes, Mrs. James (Ellen Needs)  female   
2          894       2                     Myles, Mr. Thomas Francis    male   
3          895       3                              Wirz, Mr. Albert    male   
4          896       3  Hirvonen, Mrs. Alexander (Helga E Lindqvist)  female   

    Age  SibSp  Parch   Ticket     Fare Cabin Embarked  
0  30.0      0      0   330911   7.8292    no        Q  
1  40.0      1      0   363272   7.0000    no        S  
2  60.0      0      0   240276   9.6875    no        Q  
3  20.0      0      0   315154   8.6625    no        S  
4  20.0      1      1  3101298  12.2875    no        S

In [93]:
#report train
profile_train_ml = train_data.profile_report(title='Titanic train')
#profile_train_ml.to_file(output_file="kaggle/profile_report/Titanic train ml.html")

In [94]:
profile_train_ml

## Machine learning

In [96]:
y = train_data["Survived"]

features = ["Pclass", "Sex", "SibSp", "Parch","Age"]
X = pd.get_dummies(train_data[features])
X_test = pd.get_dummies(test_data[features])

model = RandomForestClassifier(n_estimators=100, max_depth=5, random_state=1)

model.fit(X, y)

predictions = model.predict(X_test)

output = pd.DataFrame({'PassengerId': test_data.PassengerId, 'Survived': predictions})



RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
                       max_depth=5, max_features='auto', max_leaf_nodes=None,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=100,
                       n_jobs=None, oob_score=False, random_state=1, verbose=0,
                       warm_start=False)

In [97]:
output.head()

PassengerId  Survived
0          892         0
1          893         0
2          894         0
3          895         0
4          896         0

In [98]:
## Submit

In [99]:
output.to_csv('my_ml_submission.csv', index=False)
print("Your submission was successfully saved!")

Your submission was successfully saved!
